# **1. Corpus**

## Crawl URLs to extract all internal links 

**XENU Link Sleuth**  
https://home.snafu.de/tilman/xenulink.html 

*Le logiciel XENU Link Sleuth a finalement été retenu pour cette tâche* 

## Scrape textual data from crawled URLs
**BeautifulSoup HTML Parser**  
Réf : https://realpython.com/python-web-scraping-practical-introduction/

In [2]:
path = '/Users/camilledemers/Documents/03-corpus/0-listes_sites_html_pdf/'
acteur = "ramq"

La liste des URLs à scrapper pour chaque corpus est contenue dans un fichier CSV. 
On commence donc par lire le CSV pour extraire nos URLS.

In [3]:
from pandas import *

# encoding= 'ISO-8859-1' "utf-8"
path = '/Users/camilledemers/Documents/03-corpus/0-listes_sites_html_pdf/'
with open(path + acteur + '.csv', encoding= 'ISO-8859-1' ) as f:
    csv = read_csv(f, sep=';')

csv

Address             Type  \
0                         https://www.ramq.gouv.qc.ca/fr        text/html   
1                         https://www.ramq.gouv.qc.ca/en        text/html   
2                https://www.ramq.gouv.qc.ca/en/citizens        text/html   
3            https://www.ramq.gouv.qc.ca/fr/nous-joindre        text/html   
4      https://www.ramq.gouv.qc.ca/fr/citoyens/assura...        text/html   
...                                                  ...              ...   
12311  https://www.ramq.gouv.qc.ca/fr/professionnels/...        text/html   
12312  https://www.ramq.gouv.qc.ca/SiteCollectionDocu...  application/pdf   
12313  https://www.ramq.gouv.qc.ca/SiteCollectionDocu...  application/pdf   
12314  https://www.ramq.gouv.qc.ca/sites/default/file...  application/pdf   
12315  https://www.ramq.gouv.qc.ca/SiteCollectionDocu...  application/pdf   

                                                   Title Charset  \
0      Accueil | Régie de lassurance maladie du Québ...   utf-8   
1      Home | Régie de lassurance maladie du Québec ...   utf-8   
2                                                English   utf-8   
3      Nous joindre | Régie de lassurance maladie du...   utf-8   
4      Assurance maladie | Régie de lassurance malad...   utf-8   
...                                                  ...     ...   
12311                                 Infolettres | RAMQ   utf-8   
12312  Modifications apportées au Tarif des appareils...   utf-8   
12313  Facturation des réparations dappareils attrib...   utf-8   
12314  <div class="file"><span class="file_name">Télé...   utf-8   
12315  Rendez-vous santé Québec  Inscription aux ser...   utf-8   

                                             Description  
0      La Régie de lassurance maladie du Québec admi...  
1      The Régie de l&#039;assurance maladie du Québe...  
2                                                    NaN  
3      Vous avez des questions ou besoin dinformatio...  
4      La RAMQ administre le régime dassurance malad...  
...                                                  ...  
12311  La Régie de lassurance maladie du Québec admi...  
12312                                                NaN  
12313                                                NaN  
12314                                                NaN  
12315                                                NaN  

[12316 rows x 5 columns]

In [4]:
#liste = csv[csv['Type'] != 'application/pdf'] # On va scraper les PDFs avec une autre librairie que BeautifulSoup

liste = csv['Address'].tolist()
liste = [lien for lien in liste if not lien.endswith('pdf')]

In [5]:
import requests, re, ssl, os, sys
from bs4 import BeautifulSoup
#from requests.packages.urllib3.util.retry import Retry
from slugify import slugify

def getTextURL(url):    
    html = requests.get(url, headers = {'User-Agent': 'My User Agent 1.0'}, verify=False)
    html.encoding = 'utf-8'
    html = html.text
   
    soup = BeautifulSoup(html, "html.parser")
    data = soup.get_text(separator=' ').replace("\n", " ").replace("\r", " ").replace(u'\xa0', u' ')
    data = re.compile(r"\s+").sub(" ", data).strip() + "\n\n"
    
    return data

In [6]:
path = '/Users/camilledemers/Documents/03-corpus/2-data/1-fr/'

erreur = 0
for site in liste: 
    data = ""
    try: 
        text = getTextURL(site)
        data += text

        # encoding = liste[1][liste[0].index(site)] - pour prendre l'encodage qui a été extrait par le crawleur
        file_path = path + acteur + "/" + acteur + "-" + str(liste.index(site)) + ".txt"
        with open(file_path, 'w', encoding = "utf-8") as f:
            f.write(site + "\n")
            f.write(data)
        
    except Exception as e:
        print("ERROR " + " - " + site)
        print(e)
        erreur +=1 

/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  w

ERROR  - https://www.ramq.gouv.qc.ca/sites/default/files/documents/depl-assurance-medicaments-obligatoire-fr_2.pdf
cannot unpack non-iterable NoneType object


/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  w

ERROR  - https://www.ramq.gouv.qc.ca/SiteCollectionDocuments/professionnels/infolettres/2011/info106-1.pdf
local variable 'match' referenced before assignment


/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  w

...

/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  w

ERROR  - https://www.ramq.gouv.qc.ca/SiteCollectionDocuments/professionnels/infolettres/2019/info034-9.pdf
('Connection aborted.', ConnectionResetError(54, 'Connection reset by peer'))


/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  w

ERROR  - https://www.ramq.gouv.qc.ca/SiteCollectionDocuments/professionnels/infolettres/2019/info354-8.pdf
('Connection aborted.', ConnectionResetError(54, 'Connection reset by peer'))


/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/camilledemers/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1043: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ramq.gouv.qc.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  w

In [ ]:
print('Au total, il y a {} pages'.format(erreur) + ' qui n\'ont pas pu être aspirées sur les {} URLs de notre liste'.format(len(liste)))

Au total, il y a 9 pages qui n'ont pas pu être aspirées sur les 4198 URLs de notre liste


## Combine .txt files into corpora
Réf : https://www.geeksforgeeks.org/how-to-read-multiple-text-files-from-folder-in-python/

Pour comparer avec TermoStat (qui prend un seul fichier)

In [7]:
#Importer les données (fichiers .txt)
import os

acteur = "chum"
path = '/Users/camilledemers/Documents/03-corpus/2-data/1-fr/'
corpus = []
#Change the directory
os.chdir(path + acteur + "/")
len(os.listdir())

for file in os.listdir():
    if file.endswith(".txt") and not 'PDF' in file:
        file_path = path + acteur + "/" + file
        
        with open(file_path, 'r', encoding = "UTF-8") as f:
            data = f.readlines()
            corpus.append(data[1])

with open (path + acteur + "/" + acteur + '-corpus_FR.txt', 'w', encoding= 'UTF-8') as f: 
    for s in corpus:
        f.write(s) 
f.close()